In [11]:
# 
# CL-Metrics-Avalanche-DatasetA.ipynb
# 
# Author(s):
# Lan Mei <lanmei@student.ethz.ch>
#
# ======================================================================
# 
# Copyright (c) 2024 ETH Zurich.
# 
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
# 
# http://www.apache.org/licenses/LICENSE-2.0
# 
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# SPDX-License-Identifier: Apache-2.0

In [4]:
import numpy as np

from pyexpat import model
import torch
import torch.nn as nn
import torch.optim as optim
import torch as t
import torch.nn.functional as F
import json
import random
from torchvision.transforms import Compose

import os
from os import path, walk
import pandas as pd
from scipy import signal

CUR_FOLDER = os.path.abspath("")

# Dataset A downloaded from the link in README.md and put into the "data" folder
DATASET_1_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S1_1127/"
DATASET_2_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S2_1130/"
DATASET_3_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S3_1205/"
DATASET_4_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S4_1209/"
DATASET_5_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S5_1210/"
DATASET_6_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S6_1213/"
DATASET_7_PATH = CUR_FOLDER + "/data/DatasetA/2022Lan_S7_1214/"
CONFIG_PATH = CUR_FOLDER + "/config_avalanche.json"

with open(CONFIG_PATH) as fp:
    config = json.load(fp)

In [5]:
# filters
def notch_multiEEG(data,fs):
    '''
    50Hz multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''
    
    w0 = 50/(fs/2)
    Q = 30
    notch_filter_50Hz = signal.iirnotch(w0, Q)

    
    data_filt = np.zeros(data.shape)
    for chan in range(data.shape[0]):
         
        data_filt[chan, :]= signal.lfilter(*notch_filter_50Hz, data[chan, :])
        
    return data_filt

    
def bandpass_multiEEG(data, fs, f_low, f_high, order):
    '''
    Bandpass multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    f_low: float
        lower corner frequency [Hz]
    f_high: float
        upper corner_frequency [Hz]
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''

    nyq = 0.5 * fs
    low_freq = f_low / nyq
    high_freq = f_high / nyq
    filt_coef = signal.butter(N=order, Wn=[low_freq, high_freq], btype='bandpass', output='sos')
    
    for chan in range(data.shape[0]):
        data[chan, :] = signal.sosfilt(filt_coef, data[chan, :])
    return data


In [6]:
def get_data(directory, n_files, fs, filter_config, ds=1):
    '''
    Preprocess and obtain the data
    
    Params
    ------
    directory: string
        location of the csv files of data
    n_files: int
        number of files in the directory
    fs: int
        sampling frequency [Hz]
    filter_config: dictionary
        configuration of filter
    ds: int
        downsampling rate
    
    Return
    ------
    data_filt: np array 
        data and labels
    '''

    intertrial_sec = 4  # at least 4 seconds between trials
    samples_stimulus = 1950 # stimulus is 2000 samples, but some are lost due to transmission errors
    offset_sec = -5  # startpoint for the stimulus to load. choose time window (0,samples_sec) for classification in config file: t1_factor, t2_factor
    offset = int(fs * offset_sec)  # number of samples how much later than the stimulus a trial starts
    samples = samples_stimulus - offset  # number of samples of trial before cut
    intertrial = int(fs * intertrial_sec)  # number of samples in between trials
    number_of_trials = 20

    # trigger values
    trigger_left = 50
    trigger_right = 60
    trigger_nothing = 100

    # labels for classifier
    lb_nothing = 0
    lb_left = 1
    lb_right = 2

    N_ch = 8

    number_of_runs = n_files

    file_index = 0 
    runs = np.zeros((number_of_runs, number_of_trials, N_ch, samples), dtype=np.float32)
    y_runs = np.zeros((number_of_runs, number_of_trials), dtype=np.float32)

    preprocess_mean = 0
    
    valid_trials = 0
    
    for root, dirs, files in walk(directory):
        for file in files:
            print(file)
            file_path = path.join(root, file)
            df = pd.read_csv(file_path,sep=',')
            data = df.to_numpy(dtype=np.float32)
            X = np.transpose(data[:,:]) # X: [channels+triggers, samples]
            temp_afterfilt_X = X[:-1,:].copy()
            
            # Filtering
            temp_afterfilt_X = notch_multiEEG(temp_afterfilt_X, fs)
            temp_afterfilt_X = bandpass_multiEEG(temp_afterfilt_X, fs, filter_config['fc_low'], filter_config['fc_high'],
                                              filter_config['order'])
            
            # Subtracting moving avg.
            N = int(250/2)
            for i in range(N_ch):
                temp_afterfilt_X_moving_avg = np.convolve(temp_afterfilt_X[i], np.ones(N)/N, mode='same')
                temp_afterfilt_X[i] = temp_afterfilt_X[i] - temp_afterfilt_X_moving_avg
            
            trials = np.zeros((number_of_trials, N_ch, samples), dtype=np.float32)
            y = np.zeros(number_of_trials, dtype=np.float32) # to store the labels
            
            n_samples=X.shape[1] # number of samples in the run
            k = 0 # trial
            sample = 0
            
            while sample < n_samples:
                # two class classification
                if X[-1, sample] == trigger_left:  # left hand movements
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial] 

                    trials[k] = temp_filt
                    y[k] = lb_left
                    y[k] = y[k] - 1
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1
                    
                    ## Needed only for downsampling 
                    # if ds > 1:
                    #     samples_ds = int(np.ceil(samples / ds))
                    #     X_ds = np.zeros((N_ch, samples_ds), dtype=np.float64)
                    #     for chan in range(N_ch):
                    #         X_ds[chan] = signal.decimate(trial[chan, :], ds)
                    #     trial = X_ds

                elif X[-1, sample] == trigger_right:  # right hand movements
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial] 

                    trials[k] = temp_filt
                    y[k] = lb_right 
                    y[k] = y[k] - 1
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1

                    ## Needed only for downsampling 
                    # if ds > 1:
                    #     samples_ds = int(np.ceil(samples / ds))
                    #     X_ds = np.zeros((N_ch, samples_ds), dtype=np.float64)
                    #     for chan in range(N_ch):
                    #         X_ds[chan] = signal.decimate(trial[chan, :], ds)
                    #     trial = X_ds
                    
                else:
                    sample += 1  # go to the next sample

            runs[file_index] = trials
            y_runs[file_index] = y
            file_index += 1

    X = runs.reshape(number_of_runs * number_of_trials, N_ch, samples)
    y = y_runs.reshape(number_of_runs * number_of_trials)


    if ds > 1:
        samples_ds = int(np.ceil(samples / ds))
        X_ds = np.zeros((number_of_runs * number_of_trials, N_ch, samples_ds), dtype=np.float32)
        for trial in range(number_of_runs * number_of_trials):
            for chan in range(N_ch):
                X_ds[trial, chan] = signal.decimate(X[trial, chan, :], ds)
        X = X_ds
    
    if valid_trials != number_of_runs * number_of_trials:
        X_new_shape = np.zeros((valid_trials, N_ch, samples))
        y_new_shape = np.zeros((valid_trials))
        new_trial_idx = 0
        for trial_idx in range(number_of_runs * number_of_trials):
            if np.any(X[trial_idx]):
                X_new_shape[new_trial_idx] = X[trial_idx]
                y_new_shape[new_trial_idx] = y[trial_idx]
                new_trial_idx += 1
                
        X = X_new_shape
        y = y_new_shape
        
    #print(X.shape)
                
    return X,y

In [7]:
class BCI_Drone(t.utils.data.Dataset):

    def __init__(self, root, fs=500, transform=None, filter_config=None, ds=1):
        self.root = root
        self.fs = fs
        self.transform = transform
        self.filter_config = filter_config
        self.ds = ds
        self.samples, self.labels = self._load_data()

    def __len__(self):
        return len(self.samples)

    def __getitem__(self, idx):

        sample = self.samples[idx, :, :]
        label = self.labels[idx]

        if self.transform:
            sample = self.transform(sample)
        return sample, label

    def _load_data(self):
        n_files = len(os.listdir(self.root))
        X, y = get_data(self.root, n_files, self.fs, self.filter_config, self.ds)

        data_return = t.Tensor(X).to(dtype=t.float)
        class_return = t.Tensor(y).to(dtype=t.long)

        return data_return, class_return

In [8]:
class Identity(object):

    def __call__(self, sample):
        return sample


class TimeWindowPostCue(object):

    def __init__(self, fs, t1_factor, t2_factor):
        self.t1 = int(t1_factor * fs)
        self.t2 = int(t2_factor * fs)

    def __call__(self, sample):
        return sample[:, :, self.t1:self.t2]


class ReshapeTensor(object):
    def __call__(self, sample):
        return sample.view(1, sample.shape[0], sample.shape[1])
    
class ReshapeFinal(object):
    def __call__(self, sample):
        return sample.view(1, -1)

class PaddingTensor(object):
    def __init__(self, padding):
        self.padding = int(padding)

    def __call__(self, sample):
        if self.padding == 0:
            return sample

        sample_pad = np.zeros((sample.shape[0], sample.shape[1], sample.shape[2] + self.padding), dtype=np.float32)
        for i in range(sample_pad.shape[0]):
            for ch in range(sample_pad.shape[1]):
                for j in range(sample.shape[2]):
                    sample_pad[i, ch, j] = sample[i, ch, j]

        return sample_pad

def get_transform(fs, t1_factor, t2_factor, filter_config, padding=0):

    if filter_config is None:
        filter_config = {'type': None}
    elif 'type' not in filter_config:
        filter_config['type'] = 'none'

    if padding is None:
        padding = 0

    return Compose([ReshapeTensor(),
                    TimeWindowPostCue(fs, t1_factor, t2_factor),
                    PaddingTensor(padding)])

def load_data(dir_data, data_config):
    try:
        padding = data_config['padding']
    except:
        padding = 0
    transform      = get_transform(data_config['fs'], data_config['t1_factor'],
                                   data_config['t2_factor'], data_config['filter'], padding)
    loaded_data  = BCI_Drone(root=dir_data, fs=data_config['fs'], transform=transform, filter_config = data_config['filter'], ds = data_config['ds'])
    return loaded_data

In [9]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)
# using GPU
torch.cuda.manual_seed(manualSeed)
torch.cuda.manual_seed_all(manualSeed)
# using cudnn
torch.backends.cudnn.enabled = False 
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True
# dataloader number of workers 0, if > 0 background processes with their own seeds are started
nb_workers = 0
def _init_fn():
    np.random.seed(manualSeed)
    

In [ ]:
dataset_S1 = load_data(DATASET_1_PATH, config['treat']['data'])
dataset_S2_A = load_data(DATASET_2_PATH, config['treat']['data'])
dataset_S3_A = load_data(DATASET_3_PATH, config['treat']['data'])
dataset_S4_A = load_data(DATASET_4_PATH, config['treat']['data'])
dataset_S5_A = load_data(DATASET_5_PATH, config['treat']['data'])
dataset_S6_A = load_data(DATASET_6_PATH, config['treat']['data'])
dataset_S7_A = load_data(DATASET_7_PATH, config['treat']['data'])

In [9]:
from avalanche.benchmarks.utils import AvalancheDataset

from avalanche.benchmarks.utils import make_classification_dataset

#train on all data, test on last 2 runs in S1
train_size_S1 = int(0.6 * len(dataset_S1.labels))
test_size_S1 = len(dataset_S1.labels) - train_size_S1
test_dataset_S1 = torch.utils.data.Subset(dataset_S1, list(range(train_size_S1, train_size_S1+test_size_S1)))

test_dataset_S1.targets = dataset_S1.labels[test_dataset_S1.indices]

avalanche_test_dataset_S1 = make_classification_dataset(test_dataset_S1, task_labels=0)

dataset_S1.targets = dataset_S1.labels

avalanche_train_dataset_S1_full_pretrained = make_classification_dataset(dataset_S1, task_labels=0)

# t3v2 in S2
train_size_S2 = int(0.6 * len(dataset_S2_A.labels))
test_size_S2 = len(dataset_S2_A.labels) - train_size_S2
train_dataset_S2 = torch.utils.data.Subset(dataset_S2_A, list(range(0, train_size_S2)))
test_dataset_S2 = torch.utils.data.Subset(dataset_S2_A, list(range(train_size_S2, train_size_S2+test_size_S2)))

train_dataset_S2.targets = dataset_S2_A.labels[train_dataset_S2.indices]
test_dataset_S2.targets = dataset_S2_A.labels[test_dataset_S2.indices]

avalanche_train_dataset_S2 = make_classification_dataset(train_dataset_S2, task_labels=0)
avalanche_test_dataset_S2 = make_classification_dataset(test_dataset_S2, task_labels=0)

# t3v2 in S3
train_size_S3 = int(0.6 * len(dataset_S3_A.labels))
test_size_S3 = len(dataset_S3_A.labels) - train_size_S3
train_dataset_S3 = torch.utils.data.Subset(dataset_S3_A, list(range(0, train_size_S3)))
test_dataset_S3 = torch.utils.data.Subset(dataset_S3_A, list(range(train_size_S3, train_size_S3+test_size_S3)))

train_dataset_S3.targets = dataset_S3_A.labels[train_dataset_S3.indices]
test_dataset_S3.targets = dataset_S3_A.labels[test_dataset_S3.indices]

avalanche_train_dataset_S3 = make_classification_dataset(train_dataset_S3, task_labels=0)
avalanche_test_dataset_S3 = make_classification_dataset(test_dataset_S3, task_labels=0)

# t3v2 in S4
train_size_S4 = int(0.6 * len(dataset_S4_A.labels))
test_size_S4 = len(dataset_S4_A.labels) - train_size_S4
train_dataset_S4 = torch.utils.data.Subset(dataset_S4_A, list(range(0, train_size_S4)))
test_dataset_S4 = torch.utils.data.Subset(dataset_S4_A, list(range(train_size_S4, train_size_S4+test_size_S4)))

train_dataset_S4.targets = dataset_S4_A.labels[train_dataset_S4.indices]
test_dataset_S4.targets = dataset_S4_A.labels[test_dataset_S4.indices]

avalanche_train_dataset_S4 = make_classification_dataset(train_dataset_S4, task_labels=0)
avalanche_test_dataset_S4 = make_classification_dataset(test_dataset_S4, task_labels=0)

# t3v2 in S5
train_size_S5 = int(0.6 * len(dataset_S5_A.labels))
test_size_S5 = len(dataset_S5_A.labels) - train_size_S5
train_dataset_S5 = torch.utils.data.Subset(dataset_S5_A, list(range(0, train_size_S5)))
test_dataset_S5 = torch.utils.data.Subset(dataset_S5_A, list(range(train_size_S5, train_size_S5+test_size_S5)))

train_dataset_S5.targets = dataset_S5_A.labels[train_dataset_S5.indices]
test_dataset_S5.targets = dataset_S5_A.labels[test_dataset_S5.indices]

avalanche_train_dataset_S5 = make_classification_dataset(train_dataset_S5, task_labels=0)
avalanche_test_dataset_S5 = make_classification_dataset(test_dataset_S5, task_labels=0)

# t3v2 in S6
train_size_S6 = int(0.6 * len(dataset_S6_A.labels))
test_size_S6 = len(dataset_S6_A.labels) - train_size_S6
train_dataset_S6 = torch.utils.data.Subset(dataset_S6_A, list(range(0, train_size_S6)))
test_dataset_S6 = torch.utils.data.Subset(dataset_S6_A, list(range(train_size_S6, train_size_S6+test_size_S6)))

train_dataset_S6.targets = dataset_S6_A.labels[train_dataset_S6.indices]
test_dataset_S6.targets = dataset_S6_A.labels[test_dataset_S6.indices]

avalanche_train_dataset_S6 = make_classification_dataset(train_dataset_S6, task_labels=0)
avalanche_test_dataset_S6 = make_classification_dataset(test_dataset_S6, task_labels=0)

# t3v2 in S7
train_size_S7 = int(0.6 * len(dataset_S7_A.labels))
test_size_S7 = len(dataset_S7_A.labels) - train_size_S7
train_dataset_S7 = torch.utils.data.Subset(dataset_S7_A, list(range(0, train_size_S7)))
test_dataset_S7 = torch.utils.data.Subset(dataset_S7_A, list(range(train_size_S7, train_size_S7+test_size_S7)))

train_dataset_S7.targets = dataset_S7_A.labels[train_dataset_S7.indices]
test_dataset_S7.targets = dataset_S7_A.labels[test_dataset_S7.indices]

avalanche_train_dataset_S7 = make_classification_dataset(train_dataset_S7, task_labels=0)
avalanche_test_dataset_S7 = make_classification_dataset(test_dataset_S7, task_labels=0)

C:\Users\bci-admin\anaconda3\envs\avalanche\lib\site-packages\torchaudio\backend\utils.py:62: UserWarning: No audio backend is available.
  warnings.warn("No audio backend is available.")


In [25]:
from avalanche.benchmarks.generators import nc_benchmark, ni_benchmark, dataset_benchmark

scenario = dataset_benchmark(
    [avalanche_train_dataset_S1_full_pretrained, avalanche_train_dataset_S2, avalanche_train_dataset_S3, avalanche_train_dataset_S4, avalanche_train_dataset_S5, avalanche_train_dataset_S6, avalanche_train_dataset_S7], [avalanche_test_dataset_S1, avalanche_test_dataset_S2, avalanche_test_dataset_S3, avalanche_test_dataset_S4, avalanche_test_dataset_S5, avalanche_test_dataset_S6, avalanche_test_dataset_S7]
)

train_stream = scenario.train_stream

for experience in train_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    training_dataset = experience.dataset
    print('Task {} batch {} -> train'.format(task, exp_id))
    print('This batch contains', len(training_dataset), 'patterns')
    
test_stream = scenario.test_stream

for experience in test_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    test_dataset = experience.dataset
    print('Task {} batch {} -> test'.format(task, exp_id))
    print('This batch contains', len(test_dataset), 'patterns')

Task 0 batch 0 -> train
This batch contains 100 patterns
Task 0 batch 1 -> train
This batch contains 60 patterns
Task 0 batch 2 -> train
This batch contains 60 patterns
Task 0 batch 3 -> train
This batch contains 60 patterns
Task 0 batch 4 -> train
This batch contains 60 patterns
Task 0 batch 5 -> train
This batch contains 60 patterns
Task 0 batch 6 -> train
This batch contains 60 patterns
Task 0 batch 0 -> test
This batch contains 40 patterns
Task 0 batch 1 -> test
This batch contains 40 patterns
Task 0 batch 2 -> test
This batch contains 40 patterns
Task 0 batch 3 -> test
This batch contains 40 patterns
Task 0 batch 4 -> test
This batch contains 40 patterns
Task 0 batch 5 -> test
This batch contains 40 patterns
Task 0 batch 6 -> test
This batch contains 40 patterns


## MI-BMINet

In [26]:
class edgeEEGNetBaseline(t.nn.Module):

    def __init__(self, F1=8, D=2, F2=None, C=8, T=2000, N=4, Nf=64, Nf2=16, p_dropout=0.5, activation='relu', # C=8
                 dropout_type='TimeDropout2D'):
        """
        F1:           Number of spectral filters
        D:            Number of spacial filters (per spectral filter), F2 = F1 * D
        F2:           Number or None. If None, then F2 = F1 * D
        C:            Number of EEG channels
        T:            Number of time samples
        N:            Number of classes
	    Nf:           Size of temporal filter
        p_dropout:    Dropout Probability
        activation:   string, either 'elu' or 'relu'
        dropout_type: string, either 'dropout', 'SpatialDropout2d' or 'TimeDropout2D'
        """
        super(edgeEEGNetBaseline, self).__init__()

        # prepare network constants
        if F2 is None:
            F2 = F1 * D

        # check the activation input
        activation = activation.lower()
        assert activation in ['elu', 'relu']
        print("activation relu?: ", activation)

        # Prepare Dropout Type
        if dropout_type.lower() == 'dropout':
            dropout = t.nn.Dropout
        elif dropout_type.lower() == 'spatialdropout2d':
            dropout = t.nn.Dropout2d
        elif dropout_type.lower() == 'timedropout2d':
            dropout = TimeDropout2d
        else:
            raise ValueError("dropout_type must be one of SpatialDropout2d, Dropout or "
                             "WrongDropout2d")

        # store local values
        self.F1, self.D, self.F2, self.C, self.T, self.N = (F1, D, F2, C, T, N)
        self.p_dropout, self.activation = (p_dropout, activation)

        # Number of input neurons to the final fully connected layer
        n_features = (T // 8) // 8

        # Block 1
        self.conv1 = t.nn.Conv2d(1, F1, (C, 1), bias=False)
        self.batch_norm1 = t.nn.BatchNorm2d(F1, momentum=0.01, eps=0.001)
        self.conv2_pad = t.nn.ZeroPad2d((Nf//2-1, Nf//2, 0, 0)) 
        self.conv2 = t.nn.Conv2d(F1, D * F1, (1, Nf), groups=F1, bias=False)
        self.batch_norm2 = t.nn.BatchNorm2d(D * F1, momentum=0.01, eps=0.001)
        self.activation1 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool1 = t.nn.AvgPool2d((1, 8))
        self.dropout1 = t.nn.Dropout(p=p_dropout)

        # Block 2
        self.sep_conv_pad = t.nn.ZeroPad2d((7, 8, 0, 0))
        self.sep_conv1 = t.nn.Conv2d(D * F1, D * F1, (1, 16), groups=D * F1, bias=False)
        self.sep_conv2 = t.nn.Conv2d(D * F1, F2, (1, 1), bias=False)
        self.batch_norm3 = t.nn.BatchNorm2d(F2, momentum=0.01, eps=0.001)
        self.activation2 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool2 = t.nn.AvgPool2d((1, 8))
        self.dropout2 = dropout(p=p_dropout)

        # Fully connected layer (classifier)
        self.flatten = t.nn.Flatten()
        self.fc = t.nn.Linear(F2 * n_features, N, bias=True) 

        # initialize weights
        self._initialize_params() 

    def forward(self, x, with_stats=False):

        # input dimensions: (s, 1, C, T) [batchsize, 1, numb of Channels, T]

        # Block 1
        
        x = self.conv1(x)            # output dim: (s, F1, C, T-1) [batchsize, F1, 1, T]
        x = self.batch_norm1(x)      #[batchsize, F1, 1, T]
        x = self.conv2_pad(x)        
        x = self.conv2(x)            
        
        x = self.batch_norm2(x)
        x = self.activation1(x)
        x = self.pool1(x)            # output dim: (s, D * F1, 1, T // 8)
        x = self.dropout1(x)

        # Block2
        x = self.sep_conv_pad(x)
        x = self.sep_conv1(x)        # output dim: (s, D * F1, 1, T // 8 - 1)
        x = self.sep_conv2(x)        # output dim: (s, F2, 1, T // 8 - 1)
        
        x = self.batch_norm3(x)
        x = self.activation2(x)
        x = self.pool2(x)            # output dim: (s, F2, 1, T // 64)
        x = self.dropout2(x)
        

        # Classification
        x = self.flatten(x)          # output dim: (s, F2 * (T // 64))
        x = self.fc(x)               # output dim: (s, N)
        
        ## Only if we need to store weights of the network
        #if with_stats:
        #    stats = [('conv1_w', self.conv1.weight.data),
        #             ('conv2_w', self.conv2.weight.data),
        #             ('sep_conv1_w', self.sep_conv1.weight.data),
        #             ('sep_conv2_w', self.sep_conv2.weight.data),
        #             ('fc_w', self.fc.weight.data),
        #             ('fc_b', self.fc.bias.data)]
        #    return stats, x
        return x

    def forward_with_tensor_stats(self, x):
        return self.forward(x, with_stats=True)

    def _initialize_params(self, weight_init=t.nn.init.xavier_uniform_, bias_init=t.nn.init.zeros_):
        """
        Initializes all the parameters of the model

        Parameters:
         - weight_init: t.nn.init inplace function
         - bias_init:   t.nn.init inplace function

        """
        def init_weight(m):
            if isinstance(m, t.nn.Conv2d) or isinstance(m, t.nn.Linear):
                weight_init(m.weight)
            if isinstance(m, t.nn.Linear):
                bias_init(m.bias)

        self.apply(init_weight)

class Flatten(t.nn.Module):
    def forward(self, input):
        return input.view(input.size(0), -1)

class TimeDropout2d(t.nn.Dropout2d):
    """
    Dropout layer, where the last dimension is treated as channels
    """
    def __init__(self, p=0.5, inplace=False):
        """
        See t.nn.Dropout2d for parameters
        """
        super(TimeDropout2d, self).__init__(p=p, inplace=inplace)

    def forward(self, input):
        if self.training:
            input = input.permute(0, 3, 1, 2)
            input = F.dropout2d(input, self.p, True, self.inplace)
            input = input.permute(0, 2, 3, 1)
        return input

In [27]:
from avalanche.training.supervised import Naive, CWRStar, Replay, GDumb, Cumulative, LwF, GEM, AGEM, EWC  # and many more!

In [28]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)

In [29]:
from avalanche.training.utils import get_last_fc_layer, freeze_up_to
from avalanche.core import SupervisedPlugin

## Naive TL

In [24]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Naive(
        model, optimizer, loss_fn, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
        all_metrics = cl_strategy.evaluator.get_all_metrics()
        print(f"Stored metrics: {list(all_metrics.keys())}")

        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.37it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 150.0781
	Time_Epoch/train_phase/train_stream/Task000 = 1.8617
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.70it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.0820
	Time_Epoch/train_phase/train_stream/Task000 = 1.7510
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.10it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1328
	Time_Epoch/train_phase/train_stream/Task000 = 1.9567
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.68it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.6523
	Time_Epoch/train_phase/train_stream/Task000 = 1.7595
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.98it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.5508
	Time_Epoch/train_phase/train_stream/Task000 = 0.9995
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.08it/s]
Epoch 7 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.5508
	Time_Epoch/train_phase/train_stream/Task000 = 0.9848
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.86it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.4922
	Time_Epoch/train_phase/train_stream/Task000 = 1.0224
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.01it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.9023
	Time_Epoch/train_phase/train_stream/Task000 = 0.9956
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.86it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.4922
	Time_Epoch/train_phase/train_stream/Task000 = 1.0207
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.83it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 137.0547
	Time_Epoch/train_phase/train_stream/Task000 = 1.0280
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.88it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.5664
	Time_Epoch/train_phase/train_stream/Task000 = 1.0196
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.10it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.8867
	Time_Epoch/train_phase/train_stream/Task000 = 0.9830
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.40it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 0
	Time_Epoch/train_phase/train_stream/Task000 = 0.9394
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.09it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.8867
	Time_Epoch/train_phase/train_stream/Task000 = 0.9823
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8667
	To

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.94it/s]
Epoch 15 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.9492
	Time_Epoch/train_phase/train_stream/Task000 = 1.0071
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.02it/s]
Epoch 16 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.9492
	Time_Epoch/train_phase/train_stream/Task000 = 0.9955
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.93it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.9492
	Time_Epoch/train_phase/train_stream/Task000 = 1.0138
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.05it/s]
Epoch 31 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.9492
	Time_Epoch/train_phase/train_stream/Task000 = 0.9892
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.10it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 144.4375
	Time_Epoch/train_phase/train_stream/Task000 = 0.9812
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.98it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.5117
	Time_Epoch/train_phase/train_stream/Task000 = 1.0015
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

In [25]:
#Accuracy
exp_val = np.zeros((7,7,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[0,4,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[0,5,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[0,6,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,4,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[1,5,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[1,6,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,4,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[2,5,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[2,6,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,4,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[3,5,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[3,6,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[4,0,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[4,1,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[4,2,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[4,3,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[4,4,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[4,5,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[4,6,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[5,0,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[5,1,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[5,2,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[5,3,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[5,4,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[5,5,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[5,6,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[6,0,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[6,1,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[6,2,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[6,3,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[6,4,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[6,5,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[6,6,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
for i in range(7):
    for j in range(7):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
        
    print("\n")

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 62.50±2.74% 
Avg. ± Std. for exp 0 val 2: 51.00±2.00% 
Avg. ± Std. for exp 0 val 3: 58.00±5.79% 
Avg. ± Std. for exp 0 val 4: 68.50±6.63% 
Avg. ± Std. for exp 0 val 5: 54.50±6.20% 
Avg. ± Std. for exp 0 val 6: 56.00±6.44% 


Avg. ± Std. for exp 1 val 0: 71.50±5.15% 
Avg. ± Std. for exp 1 val 1: 95.00±2.74% 
Avg. ± Std. for exp 1 val 2: 58.00±1.87% 
Avg. ± Std. for exp 1 val 3: 58.50±6.04% 
Avg. ± Std. for exp 1 val 4: 56.50±5.61% 
Avg. ± Std. for exp 1 val 5: 50.50±1.00% 
Avg. ± Std. for exp 1 val 6: 50.00±0.00% 


Avg. ± Std. for exp 2 val 0: 62.00±10.17% 
Avg. ± Std. for exp 2 val 1: 66.00±5.39% 
Avg. ± Std. for exp 2 val 2: 69.50±7.81% 
Avg. ± Std. for exp 2 val 3: 49.50±1.00% 
Avg. ± Std. for exp 2 val 4: 55.00±4.18% 
Avg. ± Std. for exp 2 val 5: 60.00±6.89% 
Avg. ± Std. for exp 2 val 6: 78.50±11.47% 


Avg. ± Std. for exp 3 val 0: 60.00±5.24% 
Avg. ± Std. for exp 3 val 1: 74.00±16.02% 
Avg. ± Std. for exp 3 va

In [77]:
#Precision, Recall, Specificity
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: nan±nan% 
Precision: Avg. ± Std. for exp 0 val 6: nan±nan% 


Precision: Avg. ± Std. for exp 1 val 0: 66.95±3.88% 
Precision: Avg. ± Std. for exp 1 val 1: 96.89±2.55% 
Precision: Avg. ± Std. for exp 1 val 2: 65.17±8.29% 
Precision: Avg. ± Std. for exp 1 val 3: nan±nan% 
Precision: Avg. ± Std. for exp 1 val 4: 53.80±3.30% 
Precision: Avg. ± Std. for exp 1 val 5: 50.26±0.51% 
Precision: Avg. ± Std. for exp 1 val 6: 50.00±0.00% 


Precision: Avg. ± Std. for exp 2 val 0: nan±nan% 
Precision: Avg. ± Std. for exp 2 val 1: 91.52±16.97% 
Precision: Avg. ± Std. for exp 2 val 2: 65.09±8.98% 
Precision: Avg. ± Std. for exp 2 val 3: nan±nan% 
Precision: Avg. ± Std. for exp 2 val 4: nan±nan% 
Pre

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_18244\2474903817.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


In [7]:
#Precision, Recall, Specificity excluding NaNs
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_precision[i,j]))*100, np.nanstd(np.array(exp_precision[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_recall_sensitivity[i,j]))*100, np.nanstd(np.array(exp_recall_sensitivity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_specificity[i,j]))*100, np.nanstd(np.array(exp_specificity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: 73.41±19.81% 
Precision: Avg. ± Std. for exp 0 val 6: 95.24±6.73% 


Precision: Avg. ± Std. for exp 1 val 0: 66.95±3.88% 
Precision: Avg. ± Std. for exp 1 val 1: 96.89±2.55% 
Precision: Avg. ± Std. for exp 1 val 2: 65.17±8.29% 
Precision: Avg. ± Std. for exp 1 val 3: 100.00±0.00% 
Precision: Avg. ± Std. for exp 1 val 4: 53.80±3.30% 
Precision: Avg. ± Std. for exp 1 val 5: 50.26±0.51% 
Precision: Avg. ± Std. for exp 1 val 6: 50.00±0.00% 


Precision: Avg. ± Std. for exp 2 val 0: 81.36±14.46% 
Precision: Avg. ± Std. for exp 2 val 1: 91.52±16.97% 
Precision: Avg. ± Std. for exp 2 val 2: 65.09±8.98% 
Precision: Avg. ± Std. for exp 2 val 3: 48.48±0.00% 
Precision: Avg. ± Std. for exp 2 va

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_8504\3481318913.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
C:\Users\bci-admin\AppData\Local\Temp\ipykernel_8504\3481318913.py:43: RuntimeWarning: Mean of empty slice
  print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_precision[i,j]))*100, np.nanstd(np.array(exp_precision[i,j]))*100))
C:\Users\bci-admin\anaconda3\envs\avalanche\lib\site-packages\numpy\lib\nanfunctions.py:1872: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,


## Replay (buf=20)

In [29]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=20, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  3.41it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.7227
	Time_Epoch/train_phase/train_stream/Task000 = 2.9242
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.03it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.2812
	Time_Epoch/train_phase/train_stream/Task000 = 2.4786
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.62it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 144.5508
	Time_Epoch/train_phase/train_stream/Task000 = 2.1586
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  3.55it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 144.5508
	Time_Epoch/train_phase/train_stream/Task000 = 2.8155
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.50it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.6523
	Time_Epoch/train_phase/train_stream/Task000 = 2.3952
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9833
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.10it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 162.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.8591
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.15it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 162.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.7817
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.70it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 162.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.2232
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.82it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 162.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.1215
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.67it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 162.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.2466
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.25it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.0039
	Time_Epoch/train_phase/train_stream/Task000 = 1.8411
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9710
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.82it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.0078
	Time_Epoch/train_phase/train_stream/Task000 = 2.1220
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 49.53it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0795
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.6250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.2500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 51.15it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0781
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.8000
	Top1_ClassAcc

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.71it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.5508
	Time_Epoch/train_phase/train_stream/Task000 = 2.2068
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9815
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.62it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.1055
	Time_Epoch/train_phase/train_stream/Task000 = 2.2879
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.05it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.1055
	Time_Epoch/train_phase/train_stream/Task000 = 1.9644
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9848
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.30it/s]
Epoch 38 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 166.1055
	Time_Epoch/train_phase/train_stream/Task000 = 1.8136
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 54.76it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0719
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.8250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.7500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1 = 0.9000
-- Starting eval on experience 2 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 54.23it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.0730
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.7000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 0.5500
	Top1_ClassAcc

In [30]:
#Accuracy
exp_val = np.zeros((7,7,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[0,4,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[0,5,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[0,6,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,4,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[1,5,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[1,6,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,4,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[2,5,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[2,6,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,4,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[3,5,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[3,6,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[4,0,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[4,1,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[4,2,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[4,3,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[4,4,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[4,5,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[4,6,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[5,0,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[5,1,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[5,2,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[5,3,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[5,4,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[5,5,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[5,6,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[6,0,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[6,1,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[6,2,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[6,3,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[6,4,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[6,5,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[6,6,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
for i in range(7):
    for j in range(7):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
        
    print("\n")

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 62.50±2.74% 
Avg. ± Std. for exp 0 val 2: 51.00±2.00% 
Avg. ± Std. for exp 0 val 3: 58.00±5.79% 
Avg. ± Std. for exp 0 val 4: 68.50±6.63% 
Avg. ± Std. for exp 0 val 5: 54.50±6.20% 
Avg. ± Std. for exp 0 val 6: 56.00±6.44% 


Avg. ± Std. for exp 1 val 0: 93.50±6.04% 
Avg. ± Std. for exp 1 val 1: 95.00±3.87% 
Avg. ± Std. for exp 1 val 2: 54.50±4.00% 
Avg. ± Std. for exp 1 val 3: 60.50±4.85% 
Avg. ± Std. for exp 1 val 4: 70.50±8.28% 
Avg. ± Std. for exp 1 val 5: 71.00±9.95% 
Avg. ± Std. for exp 1 val 6: 55.00±10.12% 


Avg. ± Std. for exp 2 val 0: 84.00±4.06% 
Avg. ± Std. for exp 2 val 1: 88.50±5.83% 
Avg. ± Std. for exp 2 val 2: 70.00±10.12% 
Avg. ± Std. for exp 2 val 3: 57.50±5.92% 
Avg. ± Std. for exp 2 val 4: 69.00±8.60% 
Avg. ± Std. for exp 2 val 5: 72.00±6.20% 
Avg. ± Std. for exp 2 val 6: 82.50±11.40% 


Avg. ± Std. for exp 3 val 0: 76.00±4.64% 
Avg. ± Std. for exp 3 val 1: 84.50±10.05% 
Avg. ± Std. for exp 3 v

In [32]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    #confusion_matrix_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

#t3v2
# Not used yet, change network initialization seeds
class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    #confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    # loss function, from indiv/deamon.py
    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    # Initialize the optimizer
    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)
    # lr_scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=1000, gamma=1)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=20, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.07it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 450.9805
	Time_Epoch/train_phase/train_stream/Task000 = 1.6427
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.31it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 453.1445
	Time_Epoch/train_phase/train_stream/Task000 = 1.8821
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.93it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 450.9844
	Time_Epoch/train_phase/train_stream/Task000 = 1.6836
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.89it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 450.9844
	Time_Epoch/train_phase/train_stream/Task000 = 1.6960
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.26it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.9688
	Time_Epoch/train_phase/train_stream/Task000 = 1.8395
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9833
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.24it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.9688
	Time_Epoch/train_phase/train_stream/Task000 = 1.8513
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.24it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.9688
	Time_Epoch/train_phase/train_stream/Task000 = 1.8488
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.26it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.9688
	Time_Epoch/train_phase/train_stream/Task000 = 1.8383
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.16it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.9727
	Time_Epoch/train_phase/train_stream/Task000 = 1.9005
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.27it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 468.6680
	Time_Epoch/train_phase/train_stream/Task000 = 1.8320
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.26it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.2305
	Time_Epoch/train_phase/train_stream/Task000 = 1.8408
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9710
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.27it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.2305
	Time_Epoch/train_phase/train_stream/Task000 = 1.8323
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 60.88it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0647
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.6250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.2500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 56.67it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0705
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.8000
	Top1_ClassAcc

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.24it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.2695
	Time_Epoch/train_phase/train_stream/Task000 = 1.8495
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9815
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.25it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.9609
	Time_Epoch/train_phase/train_stream/Task000 = 1.8438
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.22it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.3359
	Time_Epoch/train_phase/train_stream/Task000 = 1.8629
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9848
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.23it/s]
Epoch 38 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.3359
	Time_Epoch/train_phase/train_stream/Task000 = 1.8573
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 48.25it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0827
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.8250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.7500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1 = 0.9000
-- Starting eval on experience 2 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 47.38it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.0847
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.7000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 0.5500
	Top1_ClassAcc

In [75]:
#Precision, Recall, Specificity
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: nan±nan% 
Precision: Avg. ± Std. for exp 0 val 6: nan±nan% 


Precision: Avg. ± Std. for exp 1 val 0: 92.27±4.79% 
Precision: Avg. ± Std. for exp 1 val 1: 93.62±5.82% 
Precision: Avg. ± Std. for exp 1 val 2: 54.13±4.57% 
Precision: Avg. ± Std. for exp 1 val 3: 89.84±12.60% 
Precision: Avg. ± Std. for exp 1 val 4: 66.38±8.37% 
Precision: Avg. ± Std. for exp 1 val 5: 65.68±8.85% 
Precision: Avg. ± Std. for exp 1 val 6: 54.55±9.13% 


Precision: Avg. ± Std. for exp 2 val 0: 81.23±7.47% 
Precision: Avg. ± Std. for exp 2 val 1: 84.75±8.99% 
Precision: Avg. ± Std. for exp 2 val 2: 68.65±12.30% 
Precision: Avg. ± Std. for exp 2 val 3: 65.17±34.69% 
Precision: Avg. ± Std. for exp 2 val 4: 69

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_18244\1831647564.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


## Replay (buf=200)

In [32]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=200, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.82it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 156.5664
	Time_Epoch/train_phase/train_stream/Task000 = 1.7176
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.79it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 156.5703
	Time_Epoch/train_phase/train_stream/Task000 = 1.7269
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.23it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 156.5742
	Time_Epoch/train_phase/train_stream/Task000 = 1.9135
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.08it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 156.5742
	Time_Epoch/train_phase/train_stream/Task000 = 1.6444
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.33it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.1562
	Time_Epoch/train_phase/train_stream/Task000 = 1.8000
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9483
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9032
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.98it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 167.3281
	Time_Epoch/train_phase/train_stream/Task000 = 2.0075
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9583
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.19it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 167.3281
	Time_Epoch/train_phase/train_stream/Task000 = 1.8838
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9831
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9508
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.22it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 167.3281
	Time_Epoch/train_phase/train_stream/Task000 = 1.8608
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.41it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 167.3359
	Time_Epoch/train_phase/train_stream/Task000 = 2.4873
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9677
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.59it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 167.3359
	Time_Epoch/train_phase/train_stream/Task000 = 2.3116
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.30it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1602
	Time_Epoch/train_phase/train_stream/Task000 = 2.6099
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9661
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.95it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1602
	Time_Epoch/train_phase/train_stream/Task000 = 3.0794
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 34.33it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.1124
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 0.9000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 34.32it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.1117
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 1.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 1.0000
	Top1_ClassAcc

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.87it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1914
	Time_Epoch/train_phase/train_stream/Task000 = 3.2000
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9455
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9846
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.96it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 143.2422
	Time_Epoch/train_phase/train_stream/Task000 = 3.0577
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9083
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.19it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.2070
	Time_Epoch/train_phase/train_stream/Task000 = 2.7296
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9333
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.81it/s]
Epoch 38 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.2070
	Time_Epoch/train_phase/train_stream/Task000 = 3.3161
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9583
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 35.41it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.1098
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.9500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1 = 1.0000
-- Starting eval on experience 2 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 37.15it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.1059
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.8250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 0.6500
	Top1_ClassAcc

In [33]:
#Accuracy
exp_val = np.zeros((7,7,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[0,4,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[0,5,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[0,6,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,4,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[1,5,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[1,6,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,4,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[2,5,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[2,6,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,4,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[3,5,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[3,6,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[4,0,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[4,1,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[4,2,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[4,3,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[4,4,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[4,5,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[4,6,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[5,0,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[5,1,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[5,2,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[5,3,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[5,4,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[5,5,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[5,6,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[6,0,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[6,1,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[6,2,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[6,3,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[6,4,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[6,5,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[6,6,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
for i in range(7):
    for j in range(7):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
        
    print("\n")

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 62.50±2.74% 
Avg. ± Std. for exp 0 val 2: 51.00±2.00% 
Avg. ± Std. for exp 0 val 3: 58.00±5.79% 
Avg. ± Std. for exp 0 val 4: 68.50±6.63% 
Avg. ± Std. for exp 0 val 5: 54.50±6.20% 
Avg. ± Std. for exp 0 val 6: 56.00±6.44% 


Avg. ± Std. for exp 1 val 0: 100.00±0.00% 
Avg. ± Std. for exp 1 val 1: 94.50±2.92% 
Avg. ± Std. for exp 1 val 2: 53.00±3.67% 
Avg. ± Std. for exp 1 val 3: 62.50±5.70% 
Avg. ± Std. for exp 1 val 4: 71.50±9.57% 
Avg. ± Std. for exp 1 val 5: 62.50±8.51% 
Avg. ± Std. for exp 1 val 6: 61.00±12.41% 


Avg. ± Std. for exp 2 val 0: 99.50±1.00% 
Avg. ± Std. for exp 2 val 1: 94.00±2.00% 
Avg. ± Std. for exp 2 val 2: 72.00±5.79% 
Avg. ± Std. for exp 2 val 3: 58.50±6.44% 
Avg. ± Std. for exp 2 val 4: 74.50±6.78% 
Avg. ± Std. for exp 2 val 5: 65.50±6.00% 
Avg. ± Std. for exp 2 val 6: 85.00±6.32% 


Avg. ± Std. for exp 3 val 0: 99.00±1.22% 
Avg. ± Std. for exp 3 val 1: 92.00±3.32% 
Avg. ± Std. for exp 3 val

In [80]:
#Precision, Recall, Specificity
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: nan±nan% 
Precision: Avg. ± Std. for exp 0 val 6: nan±nan% 


Precision: Avg. ± Std. for exp 1 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 1 val 1: 91.89±5.15% 
Precision: Avg. ± Std. for exp 1 val 2: 51.69±2.17% 
Precision: Avg. ± Std. for exp 1 val 3: 79.39±13.35% 
Precision: Avg. ± Std. for exp 1 val 4: 67.88±9.57% 
Precision: Avg. ± Std. for exp 1 val 5: 61.00±7.86% 
Precision: Avg. ± Std. for exp 1 val 6: 57.46±9.13% 


Precision: Avg. ± Std. for exp 2 val 0: 99.05±1.90% 
Precision: Avg. ± Std. for exp 2 val 1: 90.93±3.66% 
Precision: Avg. ± Std. for exp 2 val 2: 66.67±5.47% 
Precision: Avg. ± Std. for exp 2 val 3: nan±nan% 
Precision: Avg. ± Std. for exp 2 val 4: 70.59±

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_18244\1831647564.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


## LwF

In [35]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = LwF(
        model, optimizer, loss_fn, alpha=1, temperature=2, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  3.90it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.8711
	Time_Epoch/train_phase/train_stream/Task000 = 2.5465
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:03<00:00,  3.17it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.8789
	Time_Epoch/train_phase/train_stream/Task000 = 3.1519
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.13it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.2734
	Time_Epoch/train_phase/train_stream/Task000 = 2.4200
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.21it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.2227
	Time_Epoch/train_phase/train_stream/Task000 = 2.3692
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.84it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.1211
	Time_Epoch/train_phase/train_stream/Task000 = 1.5573
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.72it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.1484
	Time_Epoch/train_phase/train_stream/Task000 = 1.6089
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.60it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.1719
	Time_Epoch/train_phase/train_stream/Task000 = 1.6658
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.79it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 151.6562
	Time_Epoch/train_phase/train_stream/Task000 = 2.1517
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.28it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.1992
	Time_Epoch/train_phase/train_stream/Task000 = 1.8287
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.94it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 149.3633
	Time_Epoch/train_phase/train_stream/Task000 = 1.5200
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.39it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.3242
	Time_Epoch/train_phase/train_stream/Task000 = 1.3655
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.34it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.3242
	Time_Epoch/train_phase/train_stream/Task000 = 1.3791
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 39.79it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.1005
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.5000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 36.35it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.1084
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 1.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 1.0000
	Top1_ClassAcc

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.08it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.3242
	Time_Epoch/train_phase/train_stream/Task000 = 1.4704
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.19it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.0117
	Time_Epoch/train_phase/train_stream/Task000 = 1.4296
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.11it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.3594
	Time_Epoch/train_phase/train_stream/Task000 = 1.4588
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.32it/s]
Epoch 38 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 147.3594
	Time_Epoch/train_phase/train_stream/Task000 = 1.3838
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 43.64it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0910
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.7750
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 1.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1 = 0.5500
-- Starting eval on experience 2 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 41.08it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.0970
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.6750
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 1.0000
	Top1_ClassAcc

In [37]:
#Accuracy
exp_val = np.zeros((7,7,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[0,4,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[0,5,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[0,6,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,4,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[1,5,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[1,6,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,4,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[2,5,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[2,6,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,4,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[3,5,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[3,6,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[4,0,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[4,1,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[4,2,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[4,3,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[4,4,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[4,5,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[4,6,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[5,0,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[5,1,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[5,2,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[5,3,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[5,4,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[5,5,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[5,6,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[6,0,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[6,1,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[6,2,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[6,3,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[6,4,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[6,5,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[6,6,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
for i in range(7):
    for j in range(7):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
        
    print("\n")

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 62.50±2.74% 
Avg. ± Std. for exp 0 val 2: 51.00±2.00% 
Avg. ± Std. for exp 0 val 3: 58.00±5.79% 
Avg. ± Std. for exp 0 val 4: 68.50±6.63% 
Avg. ± Std. for exp 0 val 5: 54.50±6.20% 
Avg. ± Std. for exp 0 val 6: 56.00±6.44% 


Avg. ± Std. for exp 1 val 0: 86.50±9.03% 
Avg. ± Std. for exp 1 val 1: 87.00±3.67% 
Avg. ± Std. for exp 1 val 2: 52.50±1.58% 
Avg. ± Std. for exp 1 val 3: 66.00±8.15% 
Avg. ± Std. for exp 1 val 4: 64.50±9.67% 
Avg. ± Std. for exp 1 val 5: 57.00±9.67% 
Avg. ± Std. for exp 1 val 6: 64.00±6.44% 


Avg. ± Std. for exp 2 val 0: 73.50±7.35% 
Avg. ± Std. for exp 2 val 1: 71.00±12.21% 
Avg. ± Std. for exp 2 val 2: 72.50±10.37% 
Avg. ± Std. for exp 2 val 3: 55.00±4.74% 
Avg. ± Std. for exp 2 val 4: 55.50±8.57% 
Avg. ± Std. for exp 2 val 5: 54.50±3.32% 
Avg. ± Std. for exp 2 val 6: 65.00±11.40% 


Avg. ± Std. for exp 3 val 0: 54.00±4.64% 
Avg. ± Std. for exp 3 val 1: 66.00±13.29% 
Avg. ± Std. for exp 3 v

In [83]:
#Precision, Recall, Specificity
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: nan±nan% 
Precision: Avg. ± Std. for exp 0 val 6: nan±nan% 


Precision: Avg. ± Std. for exp 1 val 0: 81.17±11.92% 
Precision: Avg. ± Std. for exp 1 val 1: 82.53±8.24% 
Precision: Avg. ± Std. for exp 1 val 2: 51.34±0.83% 
Precision: Avg. ± Std. for exp 1 val 3: 78.03±14.16% 
Precision: Avg. ± Std. for exp 1 val 4: 60.58±7.89% 
Precision: Avg. ± Std. for exp 1 val 5: 55.59±7.10% 
Precision: Avg. ± Std. for exp 1 val 6: 61.80±9.61% 


Precision: Avg. ± Std. for exp 2 val 0: 85.49±9.86% 
Precision: Avg. ± Std. for exp 2 val 1: 91.55±11.06% 
Precision: Avg. ± Std. for exp 2 val 2: 70.58±11.68% 
Precision: Avg. ± Std. for exp 2 val 3: nan±nan% 
Precision: Avg. ± Std. for exp 2 val 4: 66.5

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_18244\1831647564.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


In [16]:
#Precision, Recall, Specificity excluding NaNs
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results_new)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_precision[i,j]))*100, np.nanstd(np.array(exp_precision[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_recall_sensitivity[i,j]))*100, np.nanstd(np.array(exp_recall_sensitivity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_specificity[i,j]))*100, np.nanstd(np.array(exp_specificity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: 73.41±19.81% 
Precision: Avg. ± Std. for exp 0 val 6: 95.24±6.73% 


Precision: Avg. ± Std. for exp 1 val 0: 81.17±11.92% 
Precision: Avg. ± Std. for exp 1 val 1: 82.53±8.24% 
Precision: Avg. ± Std. for exp 1 val 2: 51.34±0.83% 
Precision: Avg. ± Std. for exp 1 val 3: 78.03±14.16% 
Precision: Avg. ± Std. for exp 1 val 4: 60.58±7.89% 
Precision: Avg. ± Std. for exp 1 val 5: 55.59±7.10% 
Precision: Avg. ± Std. for exp 1 val 6: 61.80±9.61% 


Precision: Avg. ± Std. for exp 2 val 0: 85.49±9.86% 
Precision: Avg. ± Std. for exp 2 val 1: 91.55±11.06% 
Precision: Avg. ± Std. for exp 2 val 2: 70.58±11.68% 
Precision: Avg. ± Std. for exp 2 val 3: 85.93±9.99% 
Precision: Avg. ± Std. for exp 2 v

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_8504\3063702670.py:38: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


## EWC

In [38]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)

full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = EWC(
        model, optimizer, loss_fn, ewc_lambda=10000, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.77it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1211
	Time_Epoch/train_phase/train_stream/Task000 = 2.0942
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.4800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.50it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1250
	Time_Epoch/train_phase/train_stream/Task000 = 2.2182
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.06it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1250
	Time_Epoch/train_phase/train_stream/Task000 = 1.9759
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.48it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.1250
	Time_Epoch/train_phase/train_stream/Task000 = 2.2278
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.84it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.4414
	Time_Epoch/train_phase/train_stream/Task000 = 1.5590
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.31it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.4414
	Time_Epoch/train_phase/train_stream/Task000 = 1.8111
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.91it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.4531
	Time_Epoch/train_phase/train_stream/Task000 = 1.2188
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.87it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 148.4531
	Time_Epoch/train_phase/train_stream/Task000 = 1.2281
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.30it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 150.6328
	Time_Epoch/train_phase/train_stream/Task000 = 1.3926
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.88it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 138.8750
	Time_Epoch/train_phase/train_stream/Task000 = 1.5443
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.44it/s]
Epoch 49 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.0547
	Time_Epoch/train_phase/train_stream/Task000 = 2.4501
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.6833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.6833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.6333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7333
-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 20.19it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.18it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1133
	Time_Epoch/train_phase/train_stream/Task000 = 1.4331
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.48it/s]
Epoch 7 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 145.9570
	Time_Epoch/train_phase/train_stream/Task000 = 1.7199
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.01it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1133
	Time_Epoch/train_phase/train_stream/Task000 = 1.4956
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.55it/s]
Epoch 22 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1133
	Time_Epoch/train_phase/train_stream/Task000 = 1.3173
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.57it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1133
	Time_Epoch/train_phase/train_stream/Task000 = 3.8161
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:04<00:00,  1.40it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 146.1133
	Time_Epoch/train_phase/train_stream/Task000 = 4.2736
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.7000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 45.10it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0894
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.6750
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.3500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 42.77it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0936
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.9500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 1.0000
	Top1_ClassAcc

In [39]:
#Accuracy
exp_val = np.zeros((7,7,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[0,4,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[0,5,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[0,6,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,4,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[1,5,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[1,6,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,4,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[2,5,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[2,6,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,4,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[3,5,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[3,6,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[4,0,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[4,1,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[4,2,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[4,3,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[4,4,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[4,5,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[4,6,item_no] = (full_results[item_no][4]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[5,0,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[5,1,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[5,2,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[5,3,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[5,4,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[5,5,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[5,6,item_no] = (full_results[item_no][5]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
    exp_val[6,0,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[6,1,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[6,2,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[6,3,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[6,4,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp004'])
    exp_val[6,5,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp005'])
    exp_val[6,6,item_no] = (full_results[item_no][6]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp006'])
    
for i in range(7):
    for j in range(7):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
        
    print("\n")

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 62.50±2.74% 
Avg. ± Std. for exp 0 val 2: 51.00±2.00% 
Avg. ± Std. for exp 0 val 3: 58.00±5.79% 
Avg. ± Std. for exp 0 val 4: 68.50±6.63% 
Avg. ± Std. for exp 0 val 5: 54.50±6.20% 
Avg. ± Std. for exp 0 val 6: 56.00±6.44% 


Avg. ± Std. for exp 1 val 0: 94.00±5.15% 
Avg. ± Std. for exp 1 val 1: 84.00±7.52% 
Avg. ± Std. for exp 1 val 2: 50.00±1.58% 
Avg. ± Std. for exp 1 val 3: 62.50±5.00% 
Avg. ± Std. for exp 1 val 4: 63.50±9.03% 
Avg. ± Std. for exp 1 val 5: 77.50±7.07% 
Avg. ± Std. for exp 1 val 6: 64.50±7.81% 


Avg. ± Std. for exp 2 val 0: 89.00±11.36% 
Avg. ± Std. for exp 2 val 1: 82.00±7.97% 
Avg. ± Std. for exp 2 val 2: 59.50±3.67% 
Avg. ± Std. for exp 2 val 3: 53.00±2.92% 
Avg. ± Std. for exp 2 val 4: 64.00±10.20% 
Avg. ± Std. for exp 2 val 5: 69.00±4.64% 
Avg. ± Std. for exp 2 val 6: 79.00±4.64% 


Avg. ± Std. for exp 3 val 0: 76.00±10.20% 
Avg. ± Std. for exp 3 val 1: 62.00±8.12% 
Avg. ± Std. for exp 3 va

In [86]:
#Precision, Recall, Specificity
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: nan±nan% 
Precision: Avg. ± Std. for exp 0 val 6: nan±nan% 


Precision: Avg. ± Std. for exp 1 val 0: 90.01±7.86% 
Precision: Avg. ± Std. for exp 1 val 1: 80.17±11.90% 
Precision: Avg. ± Std. for exp 1 val 2: 50.01±0.83% 
Precision: Avg. ± Std. for exp 1 val 3: 74.19±11.92% 
Precision: Avg. ± Std. for exp 1 val 4: 61.31±9.74% 
Precision: Avg. ± Std. for exp 1 val 5: 78.05±9.06% 
Precision: Avg. ± Std. for exp 1 val 6: 66.09±11.69% 


Precision: Avg. ± Std. for exp 2 val 0: 97.82±2.68% 
Precision: Avg. ± Std. for exp 2 val 1: 96.78±4.24% 
Precision: Avg. ± Std. for exp 2 val 2: 56.37±3.08% 
Precision: Avg. ± Std. for exp 2 val 3: nan±nan% 
Precision: Avg. ± Std. for exp 2 val 4: 64.58

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_18244\1831647564.py:37: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])


In [22]:
#Precision, Recall, Specificity excluding NaNs
exp_val = np.zeros((7,7,5))

exp_tp = np.zeros((7,7,5))
exp_fp = np.zeros((7,7,5))
exp_tn = np.zeros((7,7,5))
exp_fn = np.zeros((7,7,5))
exp_precision = np.zeros((7,7,5))
exp_recall_sensitivity = np.zeros((7,7,5))
exp_specificity = np.zeros((7,7,5))

for item_no in range(len(full_results_new)):
    
    for no_sess in range(7):
        exp_tn[no_sess,0,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
        exp_tn[no_sess,4,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/0'])*20
        exp_tn[no_sess,5,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/0'])*20
        exp_tn[no_sess,6,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/0'])*20
        
        exp_tp[no_sess,0,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        exp_tp[no_sess,4,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp004/1'])*20
        exp_tp[no_sess,5,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp005/1'])*20
        exp_tp[no_sess,6,item_no] = (full_results_new[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp006/1'])*20
        
        for j in range(7):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(7):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(7):
    for j in range(7):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_precision[i,j]))*100, np.nanstd(np.array(exp_precision[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(7):
    for j in range(7):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_recall_sensitivity[i,j]))*100, np.nanstd(np.array(exp_recall_sensitivity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(7):
    for j in range(7):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.nanmean(np.array(exp_specificity[i,j]))*100, np.nanstd(np.array(exp_specificity[i,j]))*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 66.14±11.55% 
Precision: Avg. ± Std. for exp 0 val 2: 50.53±1.05% 
Precision: Avg. ± Std. for exp 0 val 3: 71.05±18.14% 
Precision: Avg. ± Std. for exp 0 val 4: 65.85±7.29% 
Precision: Avg. ± Std. for exp 0 val 5: 73.41±19.81% 
Precision: Avg. ± Std. for exp 0 val 6: 95.24±6.73% 


Precision: Avg. ± Std. for exp 1 val 0: 90.01±7.86% 
Precision: Avg. ± Std. for exp 1 val 1: 80.17±11.90% 
Precision: Avg. ± Std. for exp 1 val 2: 50.01±0.83% 
Precision: Avg. ± Std. for exp 1 val 3: 74.19±11.92% 
Precision: Avg. ± Std. for exp 1 val 4: 61.31±9.74% 
Precision: Avg. ± Std. for exp 1 val 5: 78.05±9.06% 
Precision: Avg. ± Std. for exp 1 val 6: 66.09±11.69% 


Precision: Avg. ± Std. for exp 2 val 0: 97.82±2.68% 
Precision: Avg. ± Std. for exp 2 val 1: 96.78±4.24% 
Precision: Avg. ± Std. for exp 2 val 2: 56.37±3.08% 
Precision: Avg. ± Std. for exp 2 val 3: 93.33±9.43% 
Precision: Avg. ± Std. for exp 2 va

C:\Users\bci-admin\AppData\Local\Temp\ipykernel_8504\1004731028.py:38: RuntimeWarning: invalid value encountered in scalar divide
  exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
